<a href="https://colab.research.google.com/github/xingyuYE97/Coursera_Capstone/blob/master/Week2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [0]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [0]:
neighborhoods_data = newyork_data['features']

In [0]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [0]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [7]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [8]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [9]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [20]:
CLIENT_ID = '0YGZEBTEO11BCBKF14ZPG211ZKWVWHMYNHBJEYUETAYYYNKS' # your Foursquare ID
CLIENT_SECRET = 'V11FZZQASBEZERF5SJGWMMW2JNY3R1YHHSTGJYKMSVJOYJLK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 0YGZEBTEO11BCBKF14ZPG211ZKWVWHMYNHBJEYUETAYYYNKS
CLIENT_SECRET:V11FZZQASBEZERF5SJGWMMW2JNY3R1YHHSTGJYKMSVJOYJLK


In [21]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


In [19]:
radius =1000
LIMIT=100
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius,
    LIMIT)
results = requests.get(url).json()
results

{'meta': {'code': 429,
  'errorDetail': 'Quota exceeded',
  'errorType': 'quota_exceeded',
  'requestId': '5ed4250a1835dd001b657f19'},
 'response': {}}

In [0]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [14]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

KeyError: ignored

In [15]:
results['response']

{}

In [0]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [23]:
manhattan_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [25]:
manhattan_venues.groupby('Neighborhood').count()


Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      31                      31   
Annadale                                      12                      12   
Arden Heights                                  4                       4   
Arlington                                      7                       7   
Arrochar                                      20                      20   
Arverne                                       18                      18   
Astoria                                      100                     100   
Astoria Heights                               11                      11   
Auburndale                                    16                      16   
Bath Beach                                    47                      47   
Battery Park City                             66                      66   
Bay Ridge                                     81                      81   
Bay Terrace                                   47                      47   
Baychester                                    21                      21   
Bayside                                       74                      74   
Bayswater                                      3                       3   
Bedford Park                                  39                      39   
Bedford Stuyvesant                            25                      25   
Beechhurst                                    15                      15   
Bellaire                                      11                      11   
Belle Harbor                                  17                      17   
Bellerose                                     20                      20   
Belmont                                       99                      99   
Bensonhurst                                   29                      29   
Bergen Beach                                   7                       7   
Blissville                                    15                      15   
Bloomfield                                     5                       5   
Boerum Hill                                   92                      92   
Borough Park                                  20                      20   
Breezy Point                                   4                       4   
Briarwood                                     10                      10   
Brighton Beach                                44                      44   
Broad Channel                                  5                       5   
Broadway Junction                             15                      15   
Bronxdale                                     11                      11   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   21                      21   
Bulls Head                                    47                      47   
Bushwick                                      72                      72   
Butler Manor                                   6                       6   
Cambria Heights                               11                      11   
Canarsie                                       5                       5   
Carnegie Hill                                 80                      80   
Carroll Gardens                              100                     100   
Castle Hill                                    9                       9   
Castleton Corners                             18                      18   
Central Harlem                                46                      46   
Charleston                                    31                      31   
Chelsea                                      106                     106   
Chinatown                                    100                     100   

In [0]:
from google.colab import files
manhattan_venues.to_csv('filename.csv') 
files.download('filename.csv')

In [31]:
radius=1000
LIMIT=100
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
results = requests.get(url).json()
results

{'meta': {'code': 500,
  'errorDetail': 'Foursquare servers are experiencing problems. Please retry and check status.foursquare.com for updates.',
  'errorType': 'server_error'},
 'response': {}}

In [0]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [33]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

KeyError: ignored

In [34]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

47 venues were returned by Foursquare.


In [35]:
nearby_venues

name            categories  \
0                                    Lollipops Gelato          Dessert Shop   
1                                  Ripe Kitchen & Bar  Caribbean Restaurant   
2                                     Ali's Roti Shop  Caribbean Restaurant   
3                                    Carvel Ice Cream        Ice Cream Shop   
4                         Jackie's West Indian Bakery  Caribbean Restaurant   
5                                             Jimbo's          Burger Joint   
6                                             Dunkin'            Donut Shop   
7                                            Rite Aid              Pharmacy   
8                                           Walgreens              Pharmacy   
9                                            Rite Aid              Pharmacy   
10                                             Subway        Sandwich Place   
11                                              Shell           Gas Station   
12                                         E&L Bakery                Bakery   
13                                          Walgreens              Pharmacy   
14                                           T-Mobile     Mobile Phone Shop   
15                          Popeyes Louisiana Kitchen   Fried Chicken Joint   
16                                          Fine Fare           Supermarket   
17                                     Domino's Pizza           Pizza Place   
18                                         Chase Bank                  Bank   
19                                            Dunkin'            Donut Shop   
20                                              Shell           Gas Station   
21                                           Foodtown           Supermarket   
22                                         McDonald's  Fast Food Restaurant   
23                                            Dunkin'            Donut Shop   
24                                         McDonald's  Fast Food Restaurant   
25                          Popeyes Louisiana Kitchen   Fried Chicken Joint   
26                                         McDonald's  Fast Food Restaurant   
27                                           Rite Aid              Pharmacy   
28                                       Central Deli         Deli / Bodega   
29                                   Capital One Bank                  Bank   
30                             Associated Supermarket           Supermarket   
31                                              Shell           Gas Station   
32                                           Rite Aid              Pharmacy   
33                        Dee-Lectable Pleasure Cakes                Bakery   
34                               Hong Kong China King    Chinese Restaurant   
35                         excellent taste restaurant      Asian Restaurant   
36                                           Met Food           Supermarket   
37                                            MN Deli            Bagel Shop   
38  Bee Line 42 MTA NYCT BX39 MTABus BXM11 (White ...           Bus Station   
39                      MTA Subway - Nereid Ave (2/5)         Metro Station   
40                                   Island Juice Bar             Juice Bar   
41                                         D & A Deli     Convenience Store   
42  MTA MaBSTOA Bus Bx31 / Bx39 / BxM11 at 233st S...           Bus Station   
43                      Kennedy Fried Chicken & Pizza   Fried Chicken Joint   
44                                   Seton Falls Park                  Park   
45                                              Deals        Discount Store   
46  MTA MaBSTOA Bus: Bx39 / BxM11 & Bee-Line Bus: ...           Bus Station   

          lat        lng  
0   40.894123 -73.845892  
1   40.898152 -73.838875  
2   40.894036 -73.856935  
3   40.890487 -73.848568  
4   40.889283 -73.843310  
5   40.891740 -73.858226  
6   40.890459 -73.849089  
7   40.889062 -73.842993  
8   40.896528

In [38]:
print('{} venues were returned by Foursquare.'.format(manhattan_venues.shape[0]))

9905 venues were returned by Foursquare.


In [39]:
manhattan_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [41]:
from google.colab import files
uploaded = files.upload()

Saving filename.csv to filename (1).csv


In [43]:
import pandas as pd
import io

df = pd.read_csv(io.StringIO(uploaded['filename.csv'].decode('utf-8')))
df

Unnamed: 0               Neighborhood  Neighborhood Latitude  \
0              0                  Wakefield              40.894705   
1              1                  Wakefield              40.894705   
2              2                  Wakefield              40.894705   
3              3                  Wakefield              40.894705   
4              4                  Wakefield              40.894705   
5              5                  Wakefield              40.894705   
6              6                  Wakefield              40.894705   
7              7                  Wakefield              40.894705   
8              8                  Wakefield              40.894705   
9              9                 Co-op City              40.874294   
10            10                 Co-op City              40.874294   
11            11                 Co-op City              40.874294   
12            12                 Co-op City              40.874294   
13            13                 Co-op City              40.874294   
14            14                 Co-op City              40.874294   
15            15                 Co-op City              40.874294   
16            16                 Co-op City              40.874294   
17            17                 Co-op City              40.874294   
18            18                 Co-op City              40.874294   
19            19                 Co-op City              40.874294   
20            20                 Co-op City              40.874294   
21            21                 Co-op City              40.874294   
22            22                 Co-op City              40.874294   
23            23                 Co-op City              40.874294   
24            24                 Co-op City              40.874294   
25            25                 Co-op City              40.874294   
26            26                 Co-op City              40.874294   
27            27                Eastchester              40.887556   
28            28                Eastchester              40.887556   
29            29                Eastchester              40.887556   
30            30                Eastchester              40.887556   
31            31                Eastchester              40.887556   
32            32                Eastchester              40.887556   
33            33                Eastchester              40.887556   
34            34                Eastchester              40.887556   
35            35                Eastchester              40.887556   
36            36                Eastchester              40.887556   
37            37                Eastchester              40.887556   
38            38                Eastchester              40.887556   
39            39                Eastchester              40.887556   
40            40                Eastchester              40.887556   
41            41                Eastchester              40.887556   
42            42                Eastchester              40.887556   
43            43                Eastchester              40.887556   
44            44                Eastchester              40.887556   
45            45                  Fieldston              40.895437   
46            46                  Fieldston              40.895437   
47            47                  Fieldston              40.895437   
48            48                  Fieldston              40.895437   
49            49                  Riverdale              40.890834   
50            50                  Riverdale              40.890834   
51            51                  Riverdale              40.890834   
52            52                  Riverdale              40.890834   
53            53                  Riverdale              40.890834   
54            54                  Riverdale              40.890834   
55            55                  Riverdale              40.890834   
56            56

In [0]:
thai=df[df['Venue Category']=='Thai Restaurant']

In [0]:
thai_grouped = thai.groupby('Neighborhood').count()

In [0]:
thai_grouped['Count']=thai_grouped['Venue']

In [0]:
thai_final=thai_grouped['Count']

In [58]:
thai_final.sort_values(ascending=False)

Neighborhood
Woodside              5
Elmhurst              4
Clinton Hill          4
Jackson Heights       3
Prospect Heights      3
Kensington            3
Little Italy          3
East Harlem           3
Gramercy              3
Clinton               3
Hunters Point         2
Forest Hills          2
Lenox Hill            2
Noho                  2
Cobble Hill           2
Carroll Gardens       2
Sunnyside Gardens     2
Tudor City            2
Brooklyn Heights      2
Bay Ridge             2
Chinatown             1
Downtown              1
East Village          1
East Williamsburg     1
Bulls Head            1
Flatiron              1
Boerum Hill           1
Bayside               1
Astoria               1
Fort Greene           1
Gowanus               1
Yorkville             1
Greenpoint            1
Greenwich Village     1
Woodhaven             1
Washington Heights    1
Upper West Side       1
Upper East Side       1
Turtle Bay            1
Sutton Place          1
Spuyten Duyvil        1
Sou